In [72]:
import math
import numpy as np
from Bio.PDB import PDBParser
from Bio.PDB.Polypeptide import is_aa
from Bio.PDB.DSSP import DSSP


1. Lire la structure PDB et extraire les atomes de la chaîne principale (N, CA, C, O)

In [73]:
class ReadPdbStructure:
    """Represent and extract the main chain atoms (N, CA, C, O) in the PDB structure."""

    def __init__(self, pdb_filename):
        self.pdb_filename = pdb_filename
        self.structure = self._read_pdb_structure()
        self.main_chain_atoms = self._get_main_chain_atoms()

    def _read_pdb_structure(self):
        """Lire le fichier PDB et renvoyer la structure"""
        parser = PDBParser(QUIET=True)
        structure = parser.get_structure("protein", self.pdb_filename)
        return structure
    
    def _get_main_chain_atoms(self):
        """提取每个残基的主链原子坐标 (N, CA, C, O)"""
        main_chain_atoms = []
        for model in self.structure:
            for chain in model:
                for residue in chain:
                    if is_aa(residue) and residue.has_id('N') and residue.has_id('CA') and residue.has_id('C') and residue.has_id('O'):
                        main_chain_atoms.append({
                            'residue': residue.get_resname(),
                            'res_id': residue.get_id()[1],
                            'chain': chain.get_id(),
                            'N': residue['N'].get_coord(),
                            'CA': residue['CA'].get_coord(),
                            'C': residue['C'].get_coord(),
                            'O': residue['O'].get_coord()
                        })
        return main_chain_atoms
    
    def get_main_chain_atoms(self):
        """Obtenir des informations atomiques sur la chaîne principale"""
        return self.main_chain_atoms
        

2. Calculer des hydrogènes 

In [74]:
class HydrogenBondDetector:
    """Identifier les liaisons hydrogène en fonction de l'énergie"""

    def __init__(self, main_chain_atoms):
        self.main_chain_atoms = main_chain_atoms
    
    def calculate_hydrogen_bonds(self, energy_threshold = -0.5):
        hbonds = []
        num_residues = len(self.main_chain_atoms)
        
        for i in range(num_residues):  # Iterate over donor residues
            donor_residue = self.main_chain_atoms[i]
            for j in range(i + 1, num_residues):  # Iterate over acceptor residues
                acceptor_residue = self.main_chain_atoms[j]
                
                # Calculate hydrogen bond energy
                energy = self._calculate_hydrogen_bond_energy(donor_residue, acceptor_residue)
                
                # Only consider valid hydrogen bonds (energy < threshold)
                if energy < energy_threshold:
                    hbonds.append({
                        'donor': donor_residue,  
                        'acceptor': acceptor_residue,  
                        'energy': energy
                    })

        return hbonds


    def _calculate_hydrogen_bond_energy(self, donor_residue, acceptor_residue):
        """Calculer l'énergie d'une liaison hydrogène à partir de l'équation énergétique"""
        # Ensure that necessary atoms are present in both residues
        if 'O' not in acceptor_residue or 'N' not in donor_residue or 'C' not in donor_residue:
            return float('inf')
        
        # Get atomic coordinates
        O = acceptor_residue['O']
        N = donor_residue['N']
        C = donor_residue['C']
        
        # Calculate distances between atoms
        r_ON = np.linalg.norm(O - N)
        r_CN = np.linalg.norm(C - N)
        
        # Simplified energy calculation (hydrogen atoms are not used)
        energy = 0.084 * (1/r_ON - 1/r_CN) * 332
        
        return energy


3. Attribution des structures secondaires

In [75]:
class SecondaryStructureAssigner:
    """Secondary Structure Assigner, detecting α-Helix, β-Folding, and β-Bridges based on hydrogen bonds"""

    def __init__(self, main_chain_atoms, hbonds):
        self.hbonds = hbonds
        self.main_chain_atoms = main_chain_atoms

    def assign_secondary_structure(self):
        helix = set()
        beta = set()
        beta_bridge = set()  # 新增β桥的集合

        for bond in self.hbonds:
            donor = bond['donor']
            acceptor = bond['acceptor']

            # 获取 donor 和 acceptor 的残基编号
            donor_residue_id = donor['res_id']
            acceptor_residue_id = acceptor['res_id']

            # 调试信息：打印 donor 和 acceptor 的残基编号
            print(f"Processing bond: donor_residue_id={donor_residue_id}, acceptor_residue_id={acceptor_residue_id}, diff={abs(donor_residue_id - acceptor_residue_id)}")

            # 分配二级结构：α-螺旋、β 折叠片段 和 β 桥
            if abs(donor_residue_id - acceptor_residue_id) == 4:
                print(f"Assigning helix: {donor_residue_id} <-> {acceptor_residue_id}")
                helix.add(donor_residue_id)
                helix.add(acceptor_residue_id)
            elif abs(donor_residue_id - acceptor_residue_id) > 4:
                print(f"Assigning beta sheet: {donor_residue_id} <-> {acceptor_residue_id}")
                beta.add(donor_residue_id)
                beta.add(acceptor_residue_id)
            elif abs(donor_residue_id - acceptor_residue_id) in [2, 3]:  # 新增对 β 桥的判断
                print(f"Assigning beta bridge: {donor_residue_id} <-> {acceptor_residue_id}")
                beta_bridge.add(donor_residue_id)
                beta_bridge.add(acceptor_residue_id)

        # 初始化所有残基为 'C'（环）
        secondary_structure = ['C'] * len(self.main_chain_atoms)

        # 分配 α-螺旋 ('H')、β 折叠片段 ('E') 和 β 桥 ('B')
        for index in helix:
            if index < len(secondary_structure):  # 防止索引超出范围
                secondary_structure[index] = 'H'
        for index in beta:
            if index < len(secondary_structure):  # 防止索引超出范围
                secondary_structure[index] = 'E'
        for index in beta_bridge:  # 分配 β 桥 ('B')
            if index < len(secondary_structure):
                secondary_structure[index] = 'B'

        # 调试信息：打印主链原子数量和分配结果
        print("Length of main_chain_atoms:", len(self.main_chain_atoms))
        print("Helix indices:", helix)
        print("Beta indices:", beta)
        print("Beta bridge indices:", beta_bridge)

        return secondary_structure



4. Classe pour comparer la structure secondaire prédite avec DSSP 

In [76]:
from Bio.PDB import PDBParser, DSSP

class Compare:
    """比较自定义二级结构与 DSSP 分配结果的类"""

    def __init__(self, pdb_filename, predicted_structure):
        self.pdb_filename = pdb_filename
        self.predicted_structure = predicted_structure
        self.true_structure = self._dssp_structure()

    def _dssp_structure(self):
        """从 PDB 文件中提取 DSSP 分配的二级结构。"""
        parser = PDBParser(QUIET=True)
        structure = parser.get_structure("protein", self.pdb_filename)
        
        try:
            dssp = DSSP(structure[0], self.pdb_filename)
        except Exception as e:
            print(f"DSSP 解析错误: {e}")
            return []

        dssp_structure = []
        for key in dssp.keys():
            dssp_code = dssp[key][2]  # DSSP 的二级结构代码
            if dssp_code in ('H', 'G', 'I'):  # 螺旋
                dssp_structure.append('H')
            elif dssp_code in ('E'):  # β 折叠
                dssp_structure.append('E')
            elif dssp_code in ('B'):  # β 折叠
                dssp_structure.append('B')
            else:
                dssp_structure.append('C')  # 环状结构
        return dssp_structure

    def compare(self):
        """比较预测的二级结构和 DSSP 结果，计算准确率和灵敏度。"""
        if len(self.predicted_structure) != len(self.true_structure):
            print("预测结构和真实结构长度不匹配，无法比较。")
            return None

        print(f"预测结构: {self.predicted_structure}")
        print(f"真实结构（DSSP）: {self.true_structure}")

        # 计算准确率
        tp = sum([1 for i in range(len(self.predicted_structure)) if self.predicted_structure[i] == self.true_structure[i]])
        accuracy = tp / len(self.predicted_structure)

        # 计算螺旋灵敏度
        total_helices_in_dssp = sum([1 for i in range(len(self.true_structure)) if self.true_structure[i] == 'H'])
        helix_sensitivity = (sum([1 for i in range(len(self.predicted_structure)) 
                                  if self.predicted_structure[i] == 'H' and self.true_structure[i] == 'H']) 
                             / total_helices_in_dssp) if total_helices_in_dssp > 0 else 0
        
        # 计算β折叠灵敏度
        total_beta_in_dssp = sum([1 for i in range(len(self.true_structure)) if self.true_structure[i] == 'E'])
        beta_sensitivity = (sum([1 for i in range(len(self.predicted_structure)) 
                                 if self.predicted_structure[i] == 'E' and self.true_structure[i] == 'E']) 
                            / total_beta_in_dssp) if total_beta_in_dssp > 0 else 0

        print(f"螺旋灵敏度: {helix_sensitivity}")
        print(f"β 折叠灵敏度: {beta_sensitivity}")

        return accuracy, helix_sensitivity, beta_sensitivity


Main code

In [77]:
# Main program to run the secondary structure assignment and evaluation
def main(pdb_filename):
    """Main function to run the secondary structure prediction and comparison with DSSP.
    
    Args:
        pdb_filename (str): The path to the PDB file.
    """
    # 1. Parse the PDB structure and extract main chain atoms
    pdb_structure = ReadPdbStructure(pdb_filename)
    main_chain_atoms = pdb_structure.get_main_chain_atoms()

    # Debug: print the number of atoms extracted
    print(f"Number of main chain atoms extracted: {len(main_chain_atoms)}")

    # 2. Detect hydrogen bonds
    hb_detector = HydrogenBondDetector(main_chain_atoms)
    hbonds = hb_detector.calculate_hydrogen_bonds()

    # Debug: print the number of hydrogen bonds detected
    print(f"Number of hydrogen bonds detected: {len(hbonds)}")

    # 3. Assign secondary structures based on hydrogen bonds
    # Correct parameter order: main_chain_atoms first, then hbonds
    ss_assigner = SecondaryStructureAssigner(main_chain_atoms, hbonds)
    predicted_structure = ss_assigner.assign_secondary_structure()

    # 4. Compare with DSSP results and calculate accuracy and sensitivity
    evaluator = Compare(pdb_filename, predicted_structure)
    accuracy, helix_sensitivity, beta_sensitivity = evaluator.compare()

    # Print the results
    print(f"Accuracy: {accuracy:.2f}")
    print(f"Helix Sensitivity: {helix_sensitivity:.2f}")
    print(f"Beta Sensitivity: {beta_sensitivity:.2f}")


In [78]:
# Ensure hb_detector is properly instantiated

# 1. Parse the PDB structure and extract main chain atoms
pdb_structure = ReadPdbStructure("4uw6.pdb")  # Assuming pdb_filename is defined
main_chain_atoms = pdb_structure.get_main_chain_atoms()

# 2. Detect hydrogen bonds
hb_detector = HydrogenBondDetector(main_chain_atoms)  # Instantiate hb_detector here
hbonds = hb_detector.calculate_hydrogen_bonds()  # Now you can call calculate_hydrogen_bonds()

ss_assigner = SecondaryStructureAssigner(main_chain_atoms, hbonds)
predicted_structure = ss_assigner.assign_secondary_structure()



Processing bond: donor_residue_id=4, acceptor_residue_id=5, diff=1
Processing bond: donor_residue_id=4, acceptor_residue_id=6, diff=2
Assigning beta bridge: 4 <-> 6
Processing bond: donor_residue_id=4, acceptor_residue_id=7, diff=3
Assigning beta bridge: 4 <-> 7
Processing bond: donor_residue_id=4, acceptor_residue_id=8, diff=4
Assigning helix: 4 <-> 8
Processing bond: donor_residue_id=4, acceptor_residue_id=9, diff=5
Assigning beta sheet: 4 <-> 9
Processing bond: donor_residue_id=4, acceptor_residue_id=10, diff=6
Assigning beta sheet: 4 <-> 10
Processing bond: donor_residue_id=4, acceptor_residue_id=11, diff=7
Assigning beta sheet: 4 <-> 11
Processing bond: donor_residue_id=4, acceptor_residue_id=12, diff=8
Assigning beta sheet: 4 <-> 12
Processing bond: donor_residue_id=4, acceptor_residue_id=13, diff=9
Assigning beta sheet: 4 <-> 13
Processing bond: donor_residue_id=4, acceptor_residue_id=14, diff=10
Assigning beta sheet: 4 <-> 14
Processing bond: donor_residue_id=4, acceptor_residu

In [79]:
if __name__ == "__main__":
    pdb_filename = '2v5f.pdb'  # Replace with your actual PDB file path
    main(pdb_filename)

Number of main chain atoms extracted: 103
Number of hydrogen bonds detected: 5253
Processing bond: donor_residue_id=144, acceptor_residue_id=145, diff=1
Processing bond: donor_residue_id=144, acceptor_residue_id=146, diff=2
Assigning beta bridge: 144 <-> 146
Processing bond: donor_residue_id=144, acceptor_residue_id=147, diff=3
Assigning beta bridge: 144 <-> 147
Processing bond: donor_residue_id=144, acceptor_residue_id=148, diff=4
Assigning helix: 144 <-> 148
Processing bond: donor_residue_id=144, acceptor_residue_id=149, diff=5
Assigning beta sheet: 144 <-> 149
Processing bond: donor_residue_id=144, acceptor_residue_id=150, diff=6
Assigning beta sheet: 144 <-> 150
Processing bond: donor_residue_id=144, acceptor_residue_id=151, diff=7
Assigning beta sheet: 144 <-> 151
Processing bond: donor_residue_id=144, acceptor_residue_id=152, diff=8
Assigning beta sheet: 144 <-> 152
Processing bond: donor_residue_id=144, acceptor_residue_id=153, diff=9
Assigning beta sheet: 144 <-> 153
Processing